In [1]:
from backtesting import Backtest, Strategy
from backtesting.lib import crossover, SignalStrategy, TrailingStrategy, resample_apply
from backtesting.test import SMA
from backtesting import Backtest

import matplotlib.pyplot as plt
from matplotlib.pyplot import figure
import numpy as np
import pandas as pd 
import math as m
import os, glob

C:\Users\maw\AppData\Roaming\Python\Python37\site-packages\backtesting\_plotting.py:44: UserWarning: Jupyter Notebook detected. Setting Bokeh output to notebook. This may not work in Jupyter clients without JavaScript support (e.g. PyCharm, Spyder IDE). Reset with `backtesting.set_bokeh_output(notebook=False)`.
  warnings.warn('Jupyter Notebook detected. '


Loading BokehJS ...

In [2]:
import warnings
warnings.filterwarnings("ignore")

In [3]:
pwd = os.getcwd()
datasource_path = os.path.join(pwd, r'../../../Datasets/Junio2020/procesados-regression/')
filenames = glob.glob(datasource_path + "/*.csv")
filenames.sort()
for file in filenames:
    print(filenames.index(file), ' ', os.path.basename(file))

0   R-EURUSD_FULL_1D_144F.csv
1   R-EURUSD_FULL_1D_44F.csv
2   R-EURUSD_FULL_1D_69F.csv
3   R-EURUSD_FULL_1H_44F.csv
4   R-EURUSD_FULL_1H_49F.csv
5   R-EURUSD_FULL_4H_144F.csv


In [4]:
INDEX =5

dateparse = lambda x: pd.datetime.strptime(x, '%Y-%m-%d %H:%M:%S')
DATASET = pd.read_csv(filenames[INDEX], header=0)
print(DATASET.head(5))
print(DATASET.shape)
print(DATASET.columns)


              Gmt time     Open     High      Low    Close       Volume  \
0  2004-01-01 00:00:00  1.25950  1.25965  1.25826  1.25869   19408.8998   
1  2004-01-01 04:00:00  1.25908  1.25960  1.24698  1.25910   41634.6001   
2  2004-01-01 08:00:00  1.25900  1.25953  1.25723  1.25785   23757.6001   
3  2004-01-01 12:00:00  1.25785  1.26052  1.25727  1.25911   25753.3003   
4  2004-01-01 16:00:00  1.25905  1.25968  1.25371  1.25461  234854.4999   

   Open_Bid  High_Bid  Low_Bid  Close_Bid  ...  momentum_uo  momentum_stoch  \
0   1.25934   1.25953  1.25814    1.25854  ...     0.000000       30.935252   
1   1.25898   1.25948  1.24679    1.25900  ...    86.509636       95.659037   
2   1.25884   1.25938  1.25709    1.25775  ...    78.111588       85.793212   
3   1.25775   1.26035  1.25710    1.25897  ...    74.539877       89.586411   
4   1.25890   1.25958  1.25357    1.25451  ...    60.634548       56.351551   

  momentum_stoch_signal  momentum_wr  momentum_ao  momentum_kama  \
0     

In [5]:
INICIO = 0

sub_DATASET = DATASET.iloc[-INICIO:]
print(sub_DATASET.shape)

(26494, 144)


In [6]:
class Position(SignalStrategy):
    def init(self):
        global df
        super().init()  
        self.set_signal(self.data.Position)

In [7]:
class limits(SignalStrategy, TrailingStrategy):
    buy_lim = 0.99
    sell_lim = -0.99
    
    def init(self):
        super().init()
        self.Op_Abierta = False
        
    def next(self):
        sig = self.data.Position[-1]
        if not self.Op_Abierta and sig >= self.buy_lim:
            self.buy()
            self.Op_Abierta = True
        if self.Op_Abierta and sig <= self.sell_lim:
            self.sell()
            self.Op_Abierta = False

In [8]:
class limits2(SignalStrategy, TrailingStrategy):
    buy_lim = 0.99
    sell_lim = -0.99
    
    def init(self):
        super().init()
        
    def next(self):
        sig = self.data.Position[-1]
        if  sig >= self.buy_lim:
            self.buy()
        if  sig <= self.sell_lim:
            self.sell()

In [9]:
dataN = pd.DataFrame()

class optimized(SignalStrategy, TrailingStrategy):
    buy_lim = 0.99
    sell_lim = -0.99
    
    NEG_UNO = -0.001793
    UNO = 0.001931
    
    def init(self):
        super().init()
        global dataN

        
        self.Op_Abierta = False
        dataN['Pct_Range_Close'] = self.data.Pct_Range_Close
        dataN['Class'] = 0
        
        dataN.loc[dataN['Pct_Range_Close'] <= self.NEG_UNO, 'Class'] = -1
        dataN.loc[dataN['Pct_Range_Close'] >= self.UNO, 'Class'] = 1

        dataN['Class'] = dataN['Class'].shift(-2)
        dataN['Class'].fillna(0, inplace=True)
        self.i = 0
        
        
    def next(self):
        #print('index ',str(self.i))
        #print(self.data.Close[-1])
        #print(self.data.Pct_Range_Close[-1])
        if not self.Op_Abierta and dataN['Class'][self.i] == 1:
            #print(dataN['Class'][self.i])
            #print('buy')
            self.buy()
            self.Op_Abierta = True
        elif self.Op_Abierta and dataN['Class'][self.i] == -1:
            #print(dataN['Class'][self.i])
            #print('sell')
            self.sell()
            self.Op_Abierta = False
        #else:
        #    print(' No operation')
        
        self.i=self.i+1
#        self.set_signal(pd.Series(self.Position.Class),plot=True)

In [10]:
#Optimization with SL
WITH_SL = False
CLOSE_ON_CERO = False
dataN = pd.DataFrame()

class WithStopLoss(SignalStrategy, TrailingStrategy):
    buy_lim = 0.99
    sell_lim = -0.99
    stopLoss = .009
    
    NEG_UNO = -0.001793
    UNO = 0.001931
    
    def init(self):
        super().init()
        global dataN
        global WITH_SL
        
        self.Op_Abierta = False
        dataN['Pct_Range_Close'] = self.data.Pct_Range_Close
        dataN['Class'] = 0
        
        dataN.loc[dataN['Pct_Range_Close'] <= self.NEG_UNO, 'Class'] = -1
        dataN.loc[dataN['Pct_Range_Close'] >= self.UNO, 'Class'] = 1

        dataN['Class'] = dataN['Class'].shift(-2)
        dataN['Class'].fillna(0, inplace=True)
        self.i = 0
       
        
    def next(self):
        #self.set_trailing_sl(4)
        #print('index ',str(self.i))
        #print(self.data.Close[-1])
        #print(self.data.Pct_Range_Close[-1])
        if not self.Op_Abierta and dataN['Class'][self.i] == 1:
            if (WITH_SL):
                #print('buy current Close Val: ', self.data.Close[-1])
                stopLoss = self.data.Close[-1] - self.data.Close[-1] * self.stopLoss
                #print('stop loss at: ', stopLoss)
                self.buy(sl=stopLoss)
            else:
                self.buy()
            self.Op_Abierta = True
        if self.Op_Abierta and dataN['Class'][self.i] == -1:
            if (WITH_SL):
                #print('sell current Close Val: ', self.data.Close[-1])
                stopLoss = self.data.Close[-1] + self.data.Close[-1] * self.stopLoss
                #print('stop loss at: ', stopLoss)
                self.sell(sl=stopLoss)
            else:
                self.sell()
            self.Op_Abierta = False
        if (CLOSE_ON_CERO):
            if self.Op_Abierta and dataN['Class'][self.i] == 0:
                print('Op Closed')
                self.position.close()
                self.Op_Abierta = False
        
        self.i=self.i+1
#        self.set_signal(pd.Series(self.Position.Class),plot=True)

In [11]:
bt = Backtest(sub_DATASET, optimized, cash=1000, commission=.0001)
bt.run()

Start                                       0
End                                     26493
Duration                                26493
Exposure Time [%]                           0
Equity Final [$]                      885.931
Equity Peak [$]                       1275.52
Return [%]                           -11.4069
Buy & Hold Return [%]                 11.6875
Max. Drawdown [%]                    -35.1619
Avg. Drawdown [%]                    -1.16812
Max. Drawdown Duration                  19527
Avg. Drawdown Duration                300.034
# Trades                                    0
Win Rate [%]                              NaN
Best Trade [%]                            NaN
Worst Trade [%]                           NaN
Avg. Trade [%]                            NaN
Max. Trade Duration                       NaN
Avg. Trade Duration                       NaN
Profit Factor                             NaN
Expectancy [%]                            NaN
SQN                               

In [12]:
bt.plot()

In [14]:
START = 0.0015
END = 0.0020
ITERACIONES = 30

In [15]:
UNO_VECTOR = np.linspace(START,END,ITERACIONES)
UNO_VECTOR.tolist()

[0.0015,
 0.0015172413793103448,
 0.0015344827586206897,
 0.0015517241379310344,
 0.0015689655172413794,
 0.001586206896551724,
 0.001603448275862069,
 0.0016206896551724137,
 0.0016379310344827587,
 0.0016551724137931034,
 0.0016724137931034483,
 0.001689655172413793,
 0.001706896551724138,
 0.0017241379310344827,
 0.0017413793103448277,
 0.0017586206896551724,
 0.0017758620689655173,
 0.001793103448275862,
 0.001810344827586207,
 0.0018275862068965517,
 0.0018448275862068967,
 0.0018620689655172414,
 0.0018793103448275863,
 0.001896551724137931,
 0.001913793103448276,
 0.0019310344827586207,
 0.0019482758620689654,
 0.0019655172413793106,
 0.0019827586206896553,
 0.002]

In [16]:
UNO_NEG_VECTOR = np.linspace(START*-1,END*-1,ITERACIONES)
UNO_NEG_VECTOR.tolist()

[-0.0015,
 -0.0015172413793103448,
 -0.0015344827586206897,
 -0.0015517241379310344,
 -0.0015689655172413794,
 -0.001586206896551724,
 -0.001603448275862069,
 -0.0016206896551724137,
 -0.0016379310344827587,
 -0.0016551724137931034,
 -0.0016724137931034483,
 -0.001689655172413793,
 -0.001706896551724138,
 -0.0017241379310344827,
 -0.0017413793103448277,
 -0.0017586206896551724,
 -0.0017758620689655173,
 -0.001793103448275862,
 -0.001810344827586207,
 -0.0018275862068965517,
 -0.0018448275862068967,
 -0.0018620689655172414,
 -0.0018793103448275863,
 -0.001896551724137931,
 -0.001913793103448276,
 -0.0019310344827586207,
 -0.0019482758620689654,
 -0.0019655172413793106,
 -0.0019827586206896553,
 -0.002]

In [17]:
bt.optimize(NEG_UNO = UNO_NEG_VECTOR.tolist(),
                  UNO = UNO_VECTOR.tolist(),
           maximize='Win Rate [%]',
            return_heatmap=True
           )

(Start                                       0
 End                                      5136
 Duration                                 5136
 Exposure Time [%]                           0
 Equity Final [$]                       882.65
 Equity Peak [$]                       1268.37
 Return [%]                            -11.735
 Buy & Hold Return [%]                  11.592
 Max. Drawdown [%]                    -34.9484
 Avg. Drawdown [%]                    -2.28316
 Max. Drawdown Duration                   3788
 Avg. Drawdown Duration                134.105
 # Trades                                    0
 Win Rate [%]                              NaN
 Best Trade [%]                            NaN
 Worst Trade [%]                           NaN
 Avg. Trade [%]                            NaN
 Max. Trade Duration                       NaN
 Avg. Trade Duration                       NaN
 Profit Factor                             NaN
 Expectancy [%]                            NaN
 SQN         

In [224]:
bt._results['_strategy']

<Strategy optimized(NEG_UNO=-0.001793103448275862,UNO=0.0019310344827586207)>

In [225]:
bt.plot()